In [1]:
from langchain_community.document_loaders.csv_loader import CSVLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
import pandas as pd
import langchain
import os
import openai
import ast
from langchain import OpenAI
from langchain.chains.qa_with_sources.loading import load_qa_with_sources_chain
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.document_loaders import UnstructuredURLLoader
from langchain.embeddings import OpenAIEmbeddings
from langchain.vectorstores import FAISS

In [2]:
# loader = CSVLoader(file_path="trials/brief_summaries.csv")
# data = loader.load()

In [3]:
# df= pd.read_csv("trials/brief_summaries.txt",  delimiter="|")
# df.shape

In [4]:
# df.head(20)

In [5]:
from dotenv import load_dotenv

load_dotenv()

In [6]:
llm = OpenAI(temperature=0.6, max_tokens=500)

/home/aldan/miniconda3/envs/hackupc/lib/python3.10/site-packages/langchain_core/_api/deprecation.py:119: LangChainDeprecationWarning: The class `OpenAI` was deprecated in LangChain 0.0.10 and will be removed in 0.2.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import OpenAI`.
  warn_deprecated(


In [7]:
df_trials = pd.read_csv("clinical_trials.csv")
print(df_trials.shape)
df_trials.head()

FileNotFoundError: [Errno 2] No such file or directory: 'clinical_trials.csv'

In [15]:
df_trials_filtered = df_trials[["desease_condition"]]
df_trials_filtered.head()

desease_condition
0  ['marijuana abuse', 'substance-related disorde...
1  ['marijuana abuse', 'substance-related disorde...
2  ['tuberculosis', 'latent tuberculosis', 'infec...
3  ['heart failure', 'heart diseases', 'cardiovas...
4  ['lymphoma', 'neoplasms by histologic type', '...

In [16]:
df_trials_filtered["desease_condition"].iloc[0]

"['marijuana abuse', 'substance-related disorders', 'chemically-induced disorders', 'mental disorders']"

In [17]:
def list_to_string(disease_list):
    disease_list = ast.literal_eval(disease_list)
    return ", ".join(disease_list)


df_trials_filtered["desease_condition"] = df_trials_filtered["desease_condition"].apply(
    list_to_string
)
df_trials_filtered

C:\Users\ariji\AppData\Local\Temp\ipykernel_22340\16068817.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_trials_filtered['desease_condition']= df_trials_filtered['desease_condition'].apply(list_to_string)


desease_condition
0       marijuana abuse, substance-related disorders, ...
1       marijuana abuse, substance-related disorders, ...
2       tuberculosis, latent tuberculosis, infections,...
3       heart failure, heart diseases, cardiovascular ...
4       lymphoma, neoplasms by histologic type, neopla...
...                                                   ...
440512  obesity, overweight, overnutrition, nutrition ...
440513  obesity, overweight, overnutrition, nutrition ...
440514  obesity, overweight, overnutrition, nutrition ...
440515  autistic disorder, autism spectrum disorder, c...
440516  autistic disorder, autism spectrum disorder, c...

[440517 rows x 1 columns]

In [18]:
df_trials_filtered["desease_condition"].head()

0    marijuana abuse, substance-related disorders, ...
1    marijuana abuse, substance-related disorders, ...
2    tuberculosis, latent tuberculosis, infections,...
3    heart failure, heart diseases, cardiovascular ...
4    lymphoma, neoplasms by histologic type, neopla...
Name: desease_condition, dtype: object

In [19]:
df_trials_filtered.to_csv("diseases.csv", index=False)

In [20]:
loader = CSVLoader(file_path="./diseases.csv", encoding="utf-8")
data = loader.load()
len(data)

440517

In [ ]:
embeddings = OpenAIEmbeddings()
vectorstore = FAISS.from_documents(data, embeddings)

In [ ]:
file_path = "vector_index.pkl"
with open(file_path, "wb") as f:
    pickle.dump(vectorstore, f)

In [98]:
df_trials = pd.read_csv("clinical_trials.csv")
print(df_trials.shape)
df_trials.head()

(440517, 2)


desease_condition  \
0  ['marijuana abuse', 'substance-related disorde...   
1  ['marijuana abuse', 'substance-related disorde...   
2  ['tuberculosis', 'latent tuberculosis', 'infec...   
3  ['heart failure', 'heart diseases', 'cardiovas...   
4  ['lymphoma', 'neoplasms by histologic type', '...   

                                                text  
0  nct_id: NCT03055377\nsummary: This is a 12-wee...  
1  nct_id: NCT03055377\nsummary: This is a 12-wee...  
2  nct_id: NCT03042754\nsummary: Early diagnosis ...  
3  nct_id: NCT03035123\nsummary: The EduStra-HF s...  
4  nct_id: NCT02272751\nsummary: This study will ...

In [2]:
df_trials_filtered = pd.read_csv("diseases.csv")
df_trials_filtered

desease_condition
0       marijuana abuse, substance-related disorders, ...
1       marijuana abuse, substance-related disorders, ...
2       tuberculosis, latent tuberculosis, infections,...
3       heart failure, heart diseases, cardiovascular ...
4       lymphoma, neoplasms by histologic type, neopla...
...                                                   ...
440512  obesity, overweight, overnutrition, nutrition ...
440513  obesity, overweight, overnutrition, nutrition ...
440514  obesity, overweight, overnutrition, nutrition ...
440515  autistic disorder, autism spectrum disorder, c...
440516  autistic disorder, autism spectrum disorder, c...

[440517 rows x 1 columns]

In [3]:
df2 = df_trials_filtered  # [:100]
df2.shape

(440517, 1)

In [14]:
from openai import OpenAI

client = OpenAI()

In [15]:
def get_embeddings(text):
    response = client.embeddings.create(
        input=text, dimensions=128, model="text-embedding-3-small"
    )
    return response.data[0].embedding

In [4]:
%%time
from  sentence_transformers import SentenceTransformer

encoder= SentenceTransformer("allenai-specter")
vectors= encoder.encode(df2.desease_condition, show_progress_bar=True, batch_size=64)
vectors.shape

/home/aldan/miniconda3/envs/hackupc/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/aldan/miniconda3/envs/hackupc/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/home/aldan/miniconda3/envs/hackupc/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Batches: 100%|██████████| 6884/6884 [04:32<00:00, 25.25it/s]


CPU times: user 14min 6s, sys: 1min 31s, total: 15min 37s
Wall time: 4min 48s


(440517, 768)

In [17]:
%%time
df2['embeddings']= df2['desease_condition'].apply(get_embeddings)
df2.head()

CPU times: user 261 ms, sys: 13 ms, total: 274 ms
Wall time: 26.8 s


<timed exec>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


desease_condition  \
0  marijuana abuse, substance-related disorders, ...   
1  marijuana abuse, substance-related disorders, ...   
2  tuberculosis, latent tuberculosis, infections,...   
3  heart failure, heart diseases, cardiovascular ...   
4  lymphoma, neoplasms by histologic type, neopla...   

                                          embeddings  
0  [-0.05811865255236626, -0.023393018171191216, ...  
1  [-0.0581701435148716, -0.023382455110549927, 0...  
2  [-0.03460180386900902, -0.084668830037117, 0.2...  
3  [-0.08236236125230789, -0.1235777735710144, 0....  
4  [-0.1227850392460823, 0.07155642658472061, 0.1...

In [18]:
df2['embeddings'] = vectors.astype('float32',casting='same_kind').tolist()

In [19]:
# Remove duplicate rows based on the 'nct_id' column
df2_without_duplicates = df2.drop_duplicates(subset='nct_id', keep='first')

In [24]:
df2_without_duplicates[:130077].to_csv(
    "diseases_embeddings.csv", index=False, header=True
)

In [21]:
df2_without_duplicates

desease_condition  \
0       marijuana abuse, substance-related disorders, ...   
2       tuberculosis, latent tuberculosis, infections,...   
3       heart failure, heart diseases, cardiovascular ...   
4       lymphoma, neoplasms by histologic type, neopla...   
6                            anemia, hematologic diseases   
...                                                   ...   
440506  scoliosis, spinal curvatures, spinal diseases,...   
440507  asphyxia neonatorum, asphyxia, death, patholog...   
440509  tuberculosis, helminthiasis, malnutrition, myc...   
440512  obesity, overweight, overnutrition, nutrition ...   
440515  autistic disorder, autism spectrum disorder, c...   

                                               embeddings       nct_id  
0       [-0.8323991298675537, 1.47855544090271, 0.0013...  NCT03055377  
2       [-0.43443307280540466, 0.9625586271286011, -0....  NCT03042754  
3       [-0.5791705250740051, 0.13008448481559753, 0.1...  NCT03035123  
4       [-0.1608569175004959, 0.8489153981208801, -0.5...  NCT02272751  
6       [0.21379394829273224, 0.17073844373226166, -0....  NCT00931606  
...                                                   ...          ...  
440506  [-1.20807683467865, 0.19357842206954956, 0.314...  NCT03641469  
440507  [-0.7226205468177795, 1.0146900415420532, -0.2...  NCT03621956  
440509  [-0.7196142673492432, 0.9588190913200378, 0.08...  NCT03598842  
440512  [-1.159234642982483, 0.5251776576042175, 0.237...  NCT03574103  
440515  [-0.8618993759155273, 0.7515497803688049, 0.08...  NCT03570372  

[233077 rows x 3 columns]

In [106]:
import faiss

index = faiss.IndexFlatL2(dim)
index

<faiss.swigfaiss_avx2.IndexFlatL2; proxy of <Swig Object of type 'faiss::IndexFlatL2 *' at 0x0000023493347480> >

In [108]:
search_query = "clinical trials related to alzheimers"
vec = encoder.encode(search_query)
print(vec.shape)
vec

(768,)


array([-8.82369652e-03,  8.50650743e-02,  2.08267733e-03,  6.77651772e-03,
       -2.86661759e-02, -8.71188380e-03,  6.99447095e-02,  5.04214764e-02,
        3.58386151e-02,  5.29594952e-03, -1.40875215e-02,  1.99297220e-02,
        2.27009598e-03,  2.10810862e-02,  2.66138893e-02,  1.90623086e-02,
        4.44708914e-02,  2.96202525e-02,  5.42085357e-02, -2.34859088e-03,
       -9.87798795e-02, -5.00183590e-02, -3.42465192e-02,  2.08440255e-02,
        5.31156994e-02, -1.37044629e-02,  2.92537250e-02, -2.61334293e-02,
       -1.21854078e-04, -2.36813519e-02, -3.81283499e-02, -1.79494768e-02,
       -6.29265187e-03,  1.27150817e-02,  1.19849676e-06, -7.78729608e-03,
       -1.28973828e-04,  4.01791967e-02,  4.21229303e-02, -8.72302521e-03,
        7.44823692e-03,  7.68032745e-02,  6.50246907e-03,  3.40298638e-02,
       -1.80711355e-02, -2.71878559e-02,  5.74751608e-02,  3.67745496e-02,
       -3.34868580e-02,  1.05205458e-02,  2.08975170e-02,  4.36686277e-02,
        3.47612537e-02, -

In [109]:
import numpy as np

svec = np.array(vec).reshape(1, -1)
print(svec.shape)
svec

(1, 768)


array([[-8.82369652e-03,  8.50650743e-02,  2.08267733e-03,
         6.77651772e-03, -2.86661759e-02, -8.71188380e-03,
         6.99447095e-02,  5.04214764e-02,  3.58386151e-02,
         5.29594952e-03, -1.40875215e-02,  1.99297220e-02,
         2.27009598e-03,  2.10810862e-02,  2.66138893e-02,
         1.90623086e-02,  4.44708914e-02,  2.96202525e-02,
         5.42085357e-02, -2.34859088e-03, -9.87798795e-02,
        -5.00183590e-02, -3.42465192e-02,  2.08440255e-02,
         5.31156994e-02, -1.37044629e-02,  2.92537250e-02,
        -2.61334293e-02, -1.21854078e-04, -2.36813519e-02,
        -3.81283499e-02, -1.79494768e-02, -6.29265187e-03,
         1.27150817e-02,  1.19849676e-06, -7.78729608e-03,
        -1.28973828e-04,  4.01791967e-02,  4.21229303e-02,
        -8.72302521e-03,  7.44823692e-03,  7.68032745e-02,
         6.50246907e-03,  3.40298638e-02, -1.80711355e-02,
        -2.71878559e-02,  5.74751608e-02,  3.67745496e-02,
        -3.34868580e-02,  1.05205458e-02,  2.08975170e-0

In [110]:
distances, I = index.search(svec, k=2)
print(distances, I)

[[0.7731663  0.79433584]] [[330 331]]


In [111]:
df2 = df.iloc[I[0]]
df2

desease_condition  \
330  ['alzheimer disease', 'dementia', 'brain disea...   
331  ['alzheimer disease', 'dementia', 'brain disea...   

                                                  text  
330  nct_id: NCT02164643\nsummary: A Multicenter na...  
331  nct_id: NCT02164643\nsummary: A Multicenter na...

In [113]:
df2.iloc[1].text

'nct_id: NCT02164643\nsummary: A Multicenter national longitudinal cohort study including at least 800 individuals consecutively recruited from French Research Memory Centers and followed-up over 24 month and included in Memento.\nintervention_type: Drug\nintervention_name: Florbetapir (18F)\nintervention_description: nan\nkeywords: ["Alzheimer\'s disease", \'Mild Cognitive Impairment\']'